# User Profiling

### Imports

In [1]:
import ast
import zat
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from datetime import datetime, timedelta
from zat.log_to_dataframe import LogToDataFrame
from zat.bro_log_reader import BroLogReader
from collections import defaultdict
from textblob import TextBlob
import pycountry
from collections import defaultdict
from itertools import chain
import re
import itertools
from Levenshtein import distance as levenshtein_distance
from multiprocessing import Pool

## Loading Data

In [2]:
import os

log_names_mal = ['03','04','34','39','42','51','56','62']
log_names_benign = ['irc1']
log_names = log_names_mal + log_names_benign

project_dir = '/Users/preneond/Documents/Work/Stratosphere/IRC-Research/IRC-Behavioral-Analysis/'
# project_dir = '/home/prenek/IRC-Behavioral-Analysis/'
log_dir = os.path.join(project_dir, 'zeek/logs/')
out_dir = os.path.join(project_dir, 'python/out/')

fileout_join_freq = 'join_freq.log'
fileout_lev_dist = 'lev_dist.log'

logs_fn_join = [os.path.join(log_dir,l,'irc_join.log') for l in log_names]
logs_fn_join_mal = [os.path.join(log_dir,l,'irc_join.log') for l in log_names_mal]
logs_fn_join_benign = [os.path.join(log_dir,l,'irc_join.log') for l in log_names_mal]

logs_fn_privmsg = [os.path.join(log_dir,l,'irc_privmsg.log') for l in log_names]
logs_fn_privmsg_mal = [os.path.join(log_dir,l,'irc_privmsg.log') for l in log_names_mal]
logs_fn_privmsg_benign = [os.path.join(log_dir,l,'irc_privmsg.log') for l in log_names_benign]

logs_fn_channelinfo = [os.path.join(log_dir,l,'irc_channelinfo.log') for l in log_names]
logs_fn_channelinfo_mal = [os.path.join(log_dir,l,'irc_channelinfo.log') for l in log_names_mal]
logs_fn_channelinfo_benign = [os.path.join(log_dir,l,'irc_channelinfo.log') for l in log_names_benign]

logs_fn_networkinfo = [os.path.join(log_dir,l,'irc_networkinfo.log') for l in log_names]
logs_fn_networkinfo_mal = [os.path.join(log_dir,l,'irc_networkinfo.log') for l in log_names_mal]
logs_fn_networkinfo_benign = [os.path.join(log_dir,l,'irc_networkinfo.log') for l in log_names_benign]

In [3]:
def load_logs(file):
    logs_arr = []
    if not os.path.isfile(file):
        return logs_arr
    
    reader = BroLogReader(file)
    for log in reader.readrows():
        # log is in dictionary format
        logs_arr.append(log)

    return logs_arr

In [5]:
logs_join_mal = list(map(lambda x: load_logs(x),logs_fn_join))
logs_join_benign = list(map(lambda x: load_logs(x),logs_fn_join))
logs_join = logs_join_mal + logs_join_benign

logs_privmsg_mal = list(map(lambda x: load_logs(x),logs_fn_privmsg_mal))
logs_privmsg_mal = [list(filter(lambda x: x['target'].startswith('#'), log)) for log in logs_privmsg_mal]
logs_privmsg_benign = list(map(lambda x: load_logs(x), logs_fn_privmsg_benign))
logs_privmsg_benign = [list(filter(lambda x: x['target'].startswith('#'), log)) for log in logs_privmsg_benign]
logs_privmsg = logs_privmsg_mal + logs_privmsg_benign

logs_channelinfo_mal = list(map(lambda x: load_logs(x), logs_fn_channelinfo_mal))
logs_channelinfo_benign = list(map(lambda x: load_logs(x), logs_fn_channelinfo_benign))
logs_channelinfo = logs_channelinfo_mal + logs_channelinfo_benign


logs_networkinfo_mal = list(map(lambda x: load_logs(x), logs_fn_networkinfo_mal))
logs_networkinfo_benign = list(map(lambda x: load_logs(x), logs_fn_networkinfo_benign))
logs_networkinfo = logs_networkinfo_mal + logs_networkinfo_benign

Successfully monitoring /Users/preneond/Documents/Work/Stratosphere/IRC-Research/IRC-Behavioral-Analysis/zeek/logs/04/irc_join.log...
Successfully monitoring /Users/preneond/Documents/Work/Stratosphere/IRC-Research/IRC-Behavioral-Analysis/zeek/logs/34/irc_join.log...
Successfully monitoring /Users/preneond/Documents/Work/Stratosphere/IRC-Research/IRC-Behavioral-Analysis/zeek/logs/39/irc_join.log...
Successfully monitoring /Users/preneond/Documents/Work/Stratosphere/IRC-Research/IRC-Behavioral-Analysis/zeek/logs/42/irc_join.log...
Successfully monitoring /Users/preneond/Documents/Work/Stratosphere/IRC-Research/IRC-Behavioral-Analysis/zeek/logs/51/irc_join.log...
Successfully monitoring /Users/preneond/Documents/Work/Stratosphere/IRC-Research/IRC-Behavioral-Analysis/zeek/logs/56/irc_join.log...
Successfully monitoring /Users/preneond/Documents/Work/Stratosphere/IRC-Research/IRC-Behavioral-Analysis/zeek/logs/62/irc_join.log...
Successfully monitoring /Users/preneond/Documents/Work/Stratos

### Divide logs by channels

In [14]:
from collections import defaultdict
logs_join_divided = []
for logs in logs_join:
    logs_per_channel = defaultdict(lambda: [])    
    for log in logs:
        print(log['nick'])
        logs_per_channel[log['nick']].append(log)
    logs_join_divided.append(logs_per_channel)

(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
[ARM4T|PCVREB]
(empty)
[ARM4T|PCVREB]
(empty)
[ARM4T|PCVREB]
(empty)
[ARM4T|PCVREB]
(emp

(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)
(empty)


X-r4y
X-r4y
X-r4y
X-r4y
X-r4y
coral
ctrl2
ctrl2
ctrl2
ctrl2
ctrl2
ctrl2
ctrl2
ctrl2
ctrl2
ctrl2
ctrl2
ctrl2
ctrl2
ctrl2
Gaslighterz
jiraiya
jiraiya
jiraiya
jiraiya
jiraiya
jiraiya
jiraiya
jiraiya
jiraiya
jiraiya
jiraiya
jiraiya
jiraiya
jiraiya
Lachy
Vista_
Vista_
Vista_
Vista_
Vista_
Vista_
Vista_
Vista_
Vista_
Vista_
Vista_
Vista_
Vista_
Tatto
Tatto
Tatto
Tatto
Tatto
Tatto
Tatto
Tatto
Tatto
Tatto
Tatto
Tatto
Tatto
Vista_
Tatto
Gusto_
Gusto_
Gusto_
Gusto_
Gusto_
Gusto_
Gusto_
Gusto_
Gusto_
Gusto_
Gusto_
Gusto_
Gusto_
Gusto_
Cyborg
Cyborg
Cyborg
Cyborg
Cyborg
Cyborg
Cyborg
Cyborg
Cyborg
Cyborg
Cyborg
Cyborg
Cyborg
Cyborg
Olfatto
Olfatto
Olfatto
Olfatto
Olfatto
Olfatto
Olfatto
Olfatto
Olfatto
Olfatto
Olfatto
Olfatto
Olfatto
Olfatto
Udito
Udito
Udito
Udito
Udito
Udito
Udito
Udito
Udito
Udito
Udito
Udito
Udito
Udito
Cypriot_
Cypriot_
Cypriot_
Cypriot_
Cypriot_
Cypriot_
Cypriot_
Cypriot_
help
help
help
help
help
help
help
help
help
help
help
help
help
Aquaman
Aquaman
Aquaman
Aquaman
Aquaman

`r`
nebulos
atwNEBULA
koszikFI
246GAIUY6
knur
seNEBULA
upcloud
cebula
246GAILHB
upcloud
cebula
246GAILHB
[daro]
[toyek]
246GAJB5T
Sunrise
Hope
[toyek]
246GAJB5T
Sunrise
Hope
[toyek]
Sunrise
Hope
upcloud
cebula
246GAILHB
246GAIVM7
a[z]a
246GAIVJ4
nygus
246GAIVJ2
246GAIVJ1
246GAIVJY
nebulos
246GAIUY6
knur
246GAILHB
haos
kiss
nebulos
haos
fifi
com_
kiss
Science
wests
rocky
d4riusz
[daro]
Co-Op
everdub
[daro]
[toyek]
246GAJB5T
Sunrise
Hope
[daro]
[toyek]
246GAJB5T
Sunrise
Hope
[toyek]
246GAJB5T
Sunrise
Hope
[toyek]
Sunrise
Hope
flowy
ahs_
markot
Bostik
Arelon
pyllyukko
Dronir
Undrscore
orar
Harkila
_meton
kumiduck_
mui
bitofhope
littlehope
_meton
kumiduck_
mui
bitofhope
littlehope
yoca
aakso
antti_
hkkl
DaWilho
jmax
Velzi
n1ko
zin
Pilkki
ponky
mui
gr
Annttu
yoca
aakso
antti_
hkkl
DaWilho
jmax
Velzi
n1ko
zin
Pilkki
ponky
mui
gr
Annttu
Koston
Midian
snowfake
snowfake
246GAJFJ5
246GAJFJ5
246GAJFJ5
frty
frttg
gyty
frty
frttg
gyty
frty
frttg
gyty
fr3ty
fr3ty
fr3ty
(empty)
203FAD1IE
nicku
nicku


krebbit
krebbit
krebbit
krebbit
krebbit
krebbit
krebbit
krebbit
Lumine
malu
froglegstew
Riff_
Riff_
G[R]iM
matleo
rossesred
uniera
man48
man48
man48
man48
man48
uniera
PERS|AN
(empty)
203FAD1XZ
203FAD1XZ
203FAD1XZ
PERS|AN
PERS|AN
PERS|AN
PERS|AN
(empty)
Unimatrix325
(empty)
(empty)
(empty)
Unimatrix325
Chinese_soup
Chinese_soup
pagacz_
mh|||
mh|||
Wr4ith
Wr4ith
Erbash
Ajvorl_
co_blm_tdr
g0th
xacerola
miri
ao2
ao2
Huncutka
Ibanez_
2460AE5P1
2460AE5P1
2460AE5P1
2460AE5P1
2460AE5P1
2460AE5P1
2460AE5P1
Itachi
Itachi
Itachi
Itachi
Itachi
Itachi
Itachi
Itachi
Itachi
Itachi
Itachi
Itachi
HFechs
HFechs
752OAKQMG
752OAKQMG
752OAKQMG
752OAKQMG
752OAKQMG
752OAKQMG
ulfdoz
ulfdoz
Tuna-Fish
Crawly
_sb__
_sb__
krzych
krzych
_sb_
_sb_
Rokkimies
jtodd
jtodd
xenia40
Proserpina
Proserpina
alt
alt
2460AE5QC
2460AE5QC
2460AE5QC
2460AE5QC
2460AE5QC
2460AE5QC
2460AE5QC
Itachi
Itachi
Itachi
Itachi
Itachi
Itachi
Itachi
Itachi
Itachi
Itachi
Itachi
Itachi
IRCNetWork
IRCNetWork
IRCNetWork
246GAJG8E
246GAJG8E
Bret

...

_sb__
_sb__
raccoon
raccoon
Romano51
Romano51
Romano51
Romano51
Romano51
Romano51
Romano51
Romano51
Romano51
Romano51
wolfie~
wolfie~
mattix
mattix
mattix
_sb_
_sb_
(empty)
sscaitmaintenance
(empty)
sscaitmaintenance
276DA6V4C
276DA6V4C
276DA6V4C
276DA6V4C
276DA6V4C
276DA6V4C
276DA6V4C
276DA6V4C
276DA6V4C
276DA6V4C
onto
onto
onto
onto
onto
(empty)
sscaitmaintenance
(empty)
sscaitmaintenance
2460AE52N
2460AE52N
2460AE52N
2460AE52N
2460AE52N
2460AE52N
2460AE52N
knowittall
Chef
276DA6V4H
276DA6V4H
276DA6V4H
276DA6V4H
276DA6V4H
276DA6V4H
276DA6V4H
276DA6V4H
276DA6V4H
276DA6V4H
UserATW
Creek
x|x
276SAAOO3
276SAAOO3
276SAAOO3
276SAAOO3
276SAAOO3
276SAAOO3
276SAAOO3
276SAAOO3
276SAAOO3
276SAAOO3
Poppy
Branch`
ikara
276SAAOO8
276SAAOO8
276SAAOO8
276SAAOO8
276SAAOO8
276SAAOO8
276SAAOO8
276SAAOO8
276SAAOO8
276SAAOO8
_sb__
_sb__
ytel^^
Pria_Penasar
2460AE52R
2460AE52R
2460AE52R
2460AE52R
2460AE52R
2460AE52R
2460AE52R
IRCNetWork
IRCNetWork
IRCNetWork
alt
alt
onto
onto
onto
onto
onto
Itachi
Itachi


kiss
com_
fifi
haos
tad
[m]
greg
Morderca
fach
CHANserv
Akacja
223EAAAAK
fiut
siurek
fiutek
imp
ile
Xoy
imperium
home
abys
abysek
mija
mia
od1n
skunk
opy
NRD
police
hom
SheineR
Researcher
armmy
krs
sisi
276EAC9V6
mop
byas
Pria_Penasar
Sonic
nap
Bing
andra
kidnap
arashi
Ichal_eND
wi
246GAILHB
NebulaFI
`
Pijak
free
tresor
shah
arubaPl
upJP
upmanda
belwue
arubDE
TonyMontana
gliny
realname
TexPro
George33
ddos`pt
uptime
hmc
nebulos
kiss
haos
[m]
greg
fach
CHANserv
Gandolf
223EAAAAK
zline
dd0z
Pawe1
Greyback
TonyMontana
gliny
realname
TexPro
George33
ddos`pt
uptime
hmc
nebulos
kiss
haos
[m]
greg
fach
CHANserv
Gandolf
223EAAAAK
zline
dd0z
Pawe1
Greyback
od1n
skunk
opy
NRD
hom
tresor
SheineR
Researcher
krs
276EAC9V6
_ddos`
servicee
Deific___
Suicide
348LAACBO
Coolio
elite
scarface
die
basti
ruciu
Adrian
od1n
skunk
opy
NRD
hom
tresor
SheineR
Researcher
krs
276EAC9V6
_ddos`
servicee
Deific___
Suicide
348LAACBO
Coolio
elite
scarface
die
basti
ruciu
Adrian
pilot
Anubi
|h|
rud0lf
Tourist
legion
[d

Dadko
NSA
Vatra
Emma
otis
Janosik
Valaska
Benny-
b42
lateEvening
dqd
dev_null
medvideksan
sm4sh
mkrnstein
skirit
DIS1
ojirio
wao_
zLOSTej
zLOSTej
aquarius-
jaha2x
Discord
danysek
lynsis
cisilko
_8AN_
ofelie
hany-czf
globalc
lofasz
rabe_
mzar
Riddler
gie
ext_
limbo
ali
otis
m0rrisc__
miller
grs
petrisi
th
ruupert
mato
chch
SadMan
Elef
timpo
otis
2037AAAWV
mato
chch
SadMan
Elef
timpo
otis
2037AAAWV
FilemonCZ_
Emmanuel_Chanel
zLOSTej
basher
armg
zi
zaoli
prl
Tachyon
Dadko
dpl
vykook
tdd
Elef
jv`
otis
pastika
R0m3o
kasirga
G0lf
578NAA0CG
CypRi0T
monte
itmik
wolfie
wao_
swez
Dadko
bolton
JasperWRK
Anicka
Emma
otis
Lazy
Moruska
DanN
Dadko
NSA
Vatra
Emma
otis
Janosik
Valaska
R0m3o
kasirga
G0lf
578NAA0CG
CypRi0T
banu
|_20_|-pl
peri
gaye
keci
ajda
ayse
sude
airbus
m4gn3tic
alev
azra
boeing
sema
arzu
BiRaDeR
348AAAOOS
Slumlord
sevgi
banu
man48
Qu3b3c
528GADGJ7
Unif0rm
578NAA0Q3
peri
gaye
Alf4
keci
ajda
canan
ayse
sude
airbus
banu
man48
Qu3b3c
528GADGJ7
Unif0rm
578NAA0Q3
peri
gaye
Alf4
keci
ajda


Itachi
Love7831
Love6793
Love2603
Love6234
Love7013
Love3762
Love5198
Love0837
Love9713
Love9663
Love1509
Love5225
Love3780
Love7568
Love6058
Love6907
Love3006
Love3529
Love8461
Benny-
pojir
Yossarian`
Paja
lateEvening
armg
micaai
dqd
dev_null
kakobrekla
duri
prl
hisper
monte
Liskni_si
pastika
apophys_
Zbyshek
zLOSTej
Ares
nicusor
Romania
tuvokNO
kuja
cold`
Arthur
Claudia
hostSE
GHOST_
Cristian
Anubis
kung
tuvokFI2
[hubCC]_
Grudzien22FI
PAzdzier1ikFI
hubCCfi
Love9501
Love7927
Love3056
Love7970
Love0442
Love8886
Love0365
Love2871
Love6236
Love6624
Love8450
Love6591
Love3352
Love6304
Love7728
Love8501
Love3593
Love0922
Love3149
Love1220
Love4072
Love3730
IcmPetroli
wonderwomen
flash
GelidoZzZzZ
Love35
Love39
Love41
Love47
Love50
StarLord
Rocket
Nebula
IronMan
Hulk
Thor_
lele
Drax
Gamora
Groot
Love3168
Love2464
Love9192
Love0831
Love6384
Love5074
Love3293
Love4559
Mad0uT
Love8268
Love7685
Love7387
Love9778
Love8818
Love1106
Love7473
Love9161
Love4519
Love8874
Love9501
Love7927
Love3056
Lo

203TABNF2
203TABNF1
752TAOH21
Zdenek
Tomek
0PNSAEI2K
578NAAZJH
Marian
578NAAZT6
2469ABBHJ
toyek
Fiu
intel
203TABM1M
CypRi0T
Ch4rli3
Y4nk3
Whisk33y
P4P4
Lima
Juli3t
R0m3o
G0lf
578NAA0CG
banu
Qu3b3c
528GADGJ7
Unif0rm
578NAA0Q3
peri
gaye
Alf4
keci
ajda
canan
ayse
sude
airbus
alev
azra
boeing
sema
arzu
616PAAX71
Osc4r
bir
kalifak
mh||hw
muhammat
gentoooo
lletailgug
Yuza_
BarbariScelti
ArciereMagico
BlackHat_
FreeBsd_
RedHat
`4`OPERA
`5`ROTAS
`3`TENET
`2`AREPO
cateye
nla
KickBot
UstiBotII
cherr
G0lf
578NAA0CG
Qu3b3c
528GADGJ7
Unif0rm
578NAA0Q3
ayse
Alf4
keci
canan
sude
boeing
sema
616PAAX71
Osc4r
bir
kil0
616PAAWJ4
T4ng0
X-r4y
Nov3mb3r
208BAADXT
fedaii
Br4v0
H0t3l
Indi4
siera
0PNPAK9FH
Ech0
yirmiiki
Ch4rli3
Y4nk3
Adrienn
Rita
Petra
Anita
Melinda
Anna
Emmanuel_Chanel
zLOSTej
basher
Andr
Tachyon
borifield
dpl
DIS1
vykook
tdd
pastika
Chuj
neo
Antares
Optimus
sensei
McGyver
jv`
bon-
Liskni_si
wApNo
Sheriff
Zviratko
aquarius-
rufus
BiRaDeR
Nov3mb3r
arda
208BAADXT
fedaii
Br4v0
H0t3l
Indi4
siera
0

In [11]:
logs_privmsg_benign_divided = []
for logs in logs_privmsg_benign:
    logs_per_channel = defaultdict(lambda: [])    
    for log in logs:
        logs_per_channel[log['source']].append(log)
    logs_privmsg_benign_divided.append(logs_per_channel)

heck!heck@dsl-olubng12-54fa19-87.dhcp.inet.fi
Schizzy!~prdel@20.90.broadband17.iol.cz
kanonbroom!~AndChat33@157.157.113.41
HotRom!~harris@47.133.220.111.sta.wbroadband.net.au
heck!heck@dsl-olubng12-54fa19-87.dhcp.inet.fi
heck!heck@dsl-olubng12-54fa19-87.dhcp.inet.fi
kanonbroom!~AndChat33@157.157.113.41
(empty)
HotRom!~harris@47.133.220.111.sta.wbroadband.net.au
heck!heck@dsl-olubng12-54fa19-87.dhcp.inet.fi
heck!heck@dsl-olubng12-54fa19-87.dhcp.inet.fi
kanonbroom!~AndChat33@157.157.113.41
heck!heck@dsl-olubng12-54fa19-87.dhcp.inet.fi
kanonbroom!~AndChat33@157.157.113.41
heck!heck@dsl-olubng12-54fa19-87.dhcp.inet.fi
SuA!sid13315@id-13315.charlton.irccloud.com
SuA!sid13315@id-13315.charlton.irccloud.com
heck!heck@dsl-olubng12-54fa19-87.dhcp.inet.fi
SuA!sid13315@id-13315.charlton.irccloud.com
SuA!sid13315@id-13315.charlton.irccloud.com
heck!heck@dsl-olubng12-54fa19-87.dhcp.inet.fi
Axu!~ams@solmu.cc.tut.fi
Axu!~ams@solmu.cc.tut.fi
kanonbroom!~AndChat33@157.157.113.41
SuA!sid13315@id-13315.c

Nephirus!~nephirus@91.146.121.77
Nephirus!~nephirus@91.146.121.77
dqd!id@37.205.11.166
dqd!id@37.205.11.166
dqd!id@37.205.11.166
dqd!id@37.205.11.166
MartinV!~MartinVS@235.146.230.94.awnet.cz
mr_h!~mrh@dcs.ornd.org
byzon!~m@81-35.hukot.net
byzon!~m@81-35.hukot.net
dqd!id@37.205.11.166
dqd!id@37.205.11.166
dqd!id@37.205.11.166
dqd!id@37.205.11.166
Rozhlas!pasky@2002:50f3:6e35:0:0:0:0:0
Rozhlas!pasky@2002:50f3:6e35:0:0:0:0:0
Rozhlas!pasky@2002:50f3:6e35:0:0:0:0:0
Rozhlas!pasky@2002:50f3:6e35:0:0:0:0:0
Rozhlas!pasky@2002:50f3:6e35:0:0:0:0:0
Rozhlas!pasky@2002:50f3:6e35:0:0:0:0:0
mr_h!~mrh@dcs.ornd.org
hisper!~hspt@dub.tengil.eu
hisper!~hspt@dub.tengil.eu
byzon!~m@81-35.hukot.net
byzon!~m@81-35.hukot.net
dqd!id@37.205.11.166
dqd!id@37.205.11.166
IT-News!pasky@2002:50f3:6e35:0:0:0:0:0
IT-News!pasky@2002:50f3:6e35:0:0:0:0:0
IT-News!pasky@2002:50f3:6e35:0:0:0:0:0
iHNed!pasky@2002:50f3:6e35:0:0:0:0:0
iHNed!pasky@2002:50f3:6e35:0:0:0:0:0
iHNed!pasky@2002:50f3:6e35:0:0:0:0:0
dqd!id@37.205.11.166

wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
HFechs!~HFechs@185.163.40.88
HFechs!~HFechs@185.163.40.88
Aktualne!pasky@2002:50f3:6e35:0:0:0:0:0
Aktualne!pasky@2002:50f3:6e35:0:0:0:0:0
Aktualne!pasky@2002:50f3:6e35:0:0:0:0:0
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
HFechs!~HFechs@185.163.40.88
HFechs!~HFechs@185.163.40.88
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
iDnes!pasky@2002:50f3:6e35:0:0:0:0:0
iDnes!pasky@2002:50f3:6e35:0:0:0:0:0
iDnes!pasky@2002:50f3:6e35:0:0:0:0:0
iDnes!pasky@2002:50f3:6e35:0:0:0:0:0
iDnes!pasky@2002:50f3:6e35:0

squirrel!~squirrel@ip-89-102-104-133.net.upcbroadband.cz
squirrel!~squirrel@ip-89-102-104-133.net.upcbroadband.cz
squirrel!~squirrel@ip-89-102-104-133.net.upcbroadband.cz
pojir!~pojir@109-183-159-67.customers.tmcz.cz
pojir!~pojir@109-183-159-67.customers.tmcz.cz
squirrel!~squirrel@ip-89-102-104-133.net.upcbroadband.cz
squirrel!~squirrel@ip-89-102-104-133.net.upcbroadband.cz
squirrel!~squirrel@ip-89-102-104-133.net.upcbroadband.cz
squirrel!~squirrel@ip-89-102-104-133.net.upcbroadband.cz
squirrel!~squirrel@ip-89-102-104-133.net.upcbroadband.cz
squirrel!~squirrel@ip-89-102-104-133.net.upcbroadband.cz
squirrel!~squirrel@ip-89-102-104-133.net.upcbroadband.cz
squirrel!~squirrel@ip-89-102-104-133.net.upcbroadband.cz
darecki!darek@siema.site
darecki!darek@siema.site
darecki!darek@siema.site
Parlament!pasky@2002:50f3:6e35:0:0:0:0:0
Parlament!pasky@2002:50f3:6e35:0:0:0:0:0
Parlament!pasky@2002:50f3:6e35:0:0:0:0:0
Parlament!pasky@2002:50f3:6e35:0:0:0:0:0
Parlament!pasky@2002:50f3:6e35:0:0:0:0:0
P

wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
wApNo!~wApNo@jsme.curaci.cz
SuA!sid13315@id-13315.charlton.irccloud.com
SuA!sid13315@id-13315.charlton.irccloud.com
SuA!sid13315@id-13315.charlton.irccloud.com
SuA!sid13315@id-13315.charlton.irccloud.com
Seznam!pasky@2002:50f3:6e35:0:0:0:0:0
Seznam!pasky@2002:50f3:6e35:0:0:0:0:0
Seznam!pasky@2002:50f3:6e35:0:0:0:0:0
Seznam!pasky@2002:50f3:6e35:0:0:0:0:0
Seznam!pasky@2002:50f3:6e35:0:0:0:0:0
Seznam!pasky@2002:50f3:6e35:0:0:0:0:0
Seznam!pasky@2002:50f3:6e35:0:0:0:0:0
Seznam!pasky@2002:50f3:6e35:0:0:0:0:0
redtime!redtime@curaci.cz
redtime!redtime@curaci.cz
redtime!redtime@curaci.cz
redtime!redtime@curaci.cz
redtime!redtime@curaci.cz
redtime!redtime@curaci.cz
redtime!redtime@curaci.cz
redtime!redtime@curaci.cz
wApN

...

yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
FHF!~fhf@166.172.57.183
(empty)
yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
omkxx!~jkm@91-153-249-84.elisa-laajakaista.fi
(empty)
yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
yanek!yanek@93.93.32.9
FHF!~fhf@166.172.57.183
_K_!~tom@domaci.kalhotky.net
_K_!~tom@domaci.kalhotky.net
_K_!~tom@domaci.kalhotky.net
_K_!~tom@domaci.kalhotky.net
_K_!~tom@domaci.kalhotky.net
_K_!~tom@domaci.kalhotky.net
_K_!~tom@domaci.kalhotky.net
_K_!~tom@domaci.kalhotky.net
FHF!~fhf@166.172.57.183
Novinky!pasky@2002:50f3:6e35:0:0:0:0:0
Novinky!pasky@2002:50f3:6e35:0:0:0:0:0
Novinky!pasky@2002:50f3:6e35:0:0:0:0:0
Novinky!pasky@2002:50f3:6e35:0:0:0:0:0
Novinky!pasky@2002:50f3:6e35:0:0:0:0:0
Novinky!pasky@2002:50f3:6

cuky!~cuky@ip-86-49-28-90.net.upcbroadband.cz
Echo24!pasky@2002:50f3:6e35:0:0:0:0:0
Echo24!pasky@2002:50f3:6e35:0:0:0:0:0
Echo24!pasky@2002:50f3:6e35:0:0:0:0:0
Echo24!pasky@2002:50f3:6e35:0:0:0:0:0
Echo24!pasky@2002:50f3:6e35:0:0:0:0:0
Echo24!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
Flowergirl41!44520bb8@ircip2.mibbit.com
rosses

profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
wzd_!~wzd@wizzard.ovh
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ahimsa.lamed.cz
profor!~profor@ah

heck!heck@dsl-olubng12-54fa19-87.dhcp.inet.fi
Rozhlas!pasky@2002:50f3:6e35:0:0:0:0:0
Rozhlas!pasky@2002:50f3:6e35:0:0:0:0:0
Rozhlas!pasky@2002:50f3:6e35:0:0:0:0:0
Rozhlas!pasky@2002:50f3:6e35:0:0:0:0:0
Rozhlas!pasky@2002:50f3:6e35:0:0:0:0:0
Rozhlas!pasky@2002:50f3:6e35:0:0:0:0:0
Libre___!elrond@shells.0x5e.se
Libre___!elrond@shells.0x5e.se
heck!heck@dsl-olubng12-54fa19-87.dhcp.inet.fi
Flowergirl41!44520bb8@ircip2.mibbit.com
Parlament!pasky@2002:50f3:6e35:0:0:0:0:0
Parlament!pasky@2002:50f3:6e35:0:0:0:0:0
Parlament!pasky@2002:50f3:6e35:0:0:0:0:0
Parlament!pasky@2002:50f3:6e35:0:0:0:0:0
Parlament!pasky@2002:50f3:6e35:0:0:0:0:0
Parlament!pasky@2002:50f3:6e35:0:0:0:0:0
dqd!id@37.205.11.166
dqd!id@37.205.11.166
dqd!id@37.205.11.166
dqd!id@37.205.11.166
dqd!id@37.205.11.166
HN!pasky@2002:50f3:6e35:0:0:0:0:0
HN!pasky@2002:50f3:6e35:0:0:0:0:0
HN!pasky@2002:50f3:6e35:0:0:0:0:0
HN!pasky@2002:50f3:6e35:0:0:0:0:0
HN!pasky@2002:50f3:6e35:0:0:0:0:0
HN!pasky@2002:50f3:6e35:0:0:0:0:0
dqd!id@37.205.11.

burneddi!~mugi@baka.fi
ShadowKoala!~Shadow@1.128.110.239
Dronir!dronir@kapsi.fi
Dronir!dronir@kapsi.fi
Dronir!dronir@kapsi.fi
Dronir!dronir@kapsi.fi
Dronir!dronir@kapsi.fi
Dronir!dronir@kapsi.fi
Dronir!dronir@kapsi.fi
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
slashdot!pasky@2002:50f3:6e35:0:0:0:0:0
bbb98!b9d4ab10@webchat.ircnet.net
bbb98!b9d4ab10@webchat.ircnet.net
bbb98!b9d4ab10@webchat.ircnet.net


In [12]:
logs_privmsg_mal_divided = []
for logs in logs_privmsg_mal:
    logs_per_channel = defaultdict(lambda: [])    
    for log in logs:
        print(log['source'])
        logs_per_channel[log['source']].append(log)
    logs_privmsg_mal_divided.append(logs_per_channel)

AmpAttacks!AmpAttacks@Summit.gov.GoV
AmpAttacks!AmpAttacks@Summit.gov.GoV
Spoof!Spoof@Summit.gov.GoV
Spoof!Spoof@Summit.gov.GoV
Spoof!Spoof@Summit.gov.GoV
Tragedy!Erradic@Summit.gov.GoV
Tragedy!Erradic@Summit.gov.GoV
Tragedy!Erradic@Summit.gov.GoV
Tragedy!Erradic@Summit.gov.GoV
AmpAttacks!AmpAttacks@Summit.gov.GoV
Tragedy!Erradic@Summit.gov.GoV
Tragedy!Erradic@Summit.gov.GoV
Tragedy!Erradic@Summit.gov.GoV
Tragedy!Erradic@Summit.gov.GoV
Tragedy!Erradic@Summit.gov.GoV
Tragedy!Erradic@Summit.gov.GoV
Tragedy!Erradic@Summit.gov.GoV
AmpAttacks!AmpAttacks@Summit.gov.GoV
Spoof!Spoof@Summit.gov.GoV
AmpAttacks!AmpAttacks@Summit.gov.GoV
Tragedy!Erradic@Summit.gov.GoV
Spoof!Spoof@Summit.gov.GoV
Spoof!Spoof@Summit.gov.GoV
AmpAttacks!AmpAttacks@Summit.gov.GoV
AmpAttacks!AmpAttacks@Summit.gov.GoV
Tragedy!Erradic@Summit.gov.GoV
AmpAttacks!AmpAttacks@Summit.gov.GoV
AmpAttacks!AmpAttacks@Summit.gov.GoV
AmpAttacks!AmpAttacks@Summit.gov.GoV
Tragedy!Erradic@Summit.gov.GoV
Spoof!Spoof@Summit.gov.GoV
Spoof!S

b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP
b4sh!b4sh@1F0B5DD7.CDEDE876.871C443B.IP


## Creating a DataFrame for saving all features

In [29]:
cols = ['pcap', 'user_h', 'channels_join_count', 'lang', 'msg_lev_dist_mean', 'msg_lev_dist_std',
        'msg_periodicity', 'msg_frequency', 'spec_chars_mean', 'word_entropy', 'active_channels',
        'nick_changes_count', 'network_info-num_services', 'network_info-num_users', 'malicious']

df_mal = pd.DataFrame(columns=cols)

for ln, logs_div in zip(log_names_mal, logs_privmsg_mal_divided):
    for user_h in logs_div:
        df_mal = df_mal.append({'pcap': ln, 'user_h':user_h}, ignore_index=True)

df_benign = pd.DataFrame(columns=cols)
for ln, logs_div in zip(log_names_benign, logs_privmsg_benign_divided):
    for user_h in logs_div:
        df_benign = df_benign.append({'pcap': ln, 'user_h':user_h}, ignore_index=True)

df_benign.head()

pcap           user_h channels_join_count lang msg_lev_dist_mean  \
0  irc1     195.91.66.10                 NaN  NaN               NaN   
1  irc1  195.113.136.240                 NaN  NaN               NaN   
2  irc1     147.32.80.73                 NaN  NaN               NaN   
3  irc1     80.79.26.115                 NaN  NaN               NaN   
4  irc1    85.159.104.98                 NaN  NaN               NaN   

  msg_lev_dist_std msg_periodicity msg_frequency spec_chars_mean word_entropy  \
0              NaN             NaN           NaN             NaN          NaN   
1              NaN             NaN           NaN             NaN          NaN   
2              NaN             NaN           NaN             NaN          NaN   
3              NaN             NaN           NaN             NaN          NaN   
4              NaN             NaN           NaN             NaN          NaN   

  active_channels nick_changes_count network_info-num_services  \
0             NaN                NaN                       NaN   
1             NaN                NaN                       NaN   
2             NaN                NaN                       NaN   
3             NaN                NaN                       NaN   
4             NaN                NaN                       NaN   

  network_info-num_users malicious  
0                    NaN       NaN  
1                    NaN       NaN  
2                    NaN       NaN  
3                    NaN       NaN  
4                    NaN       NaN

## Number of Joined Channels

In [9]:
# import json

# def ircjoin_compute(logs):
#     if len(logs) == 0:
#         return None, None

#     logs_ts = list(map(lambda x: x['ts'].date(), logs))

#     # first ts of join command
#     ts_min = min(logs_ts)
#     ts_max = max(logs_ts)
# #     print('min date: {}, max date: {}'.format(ts_min, ts_max))
#     span = ts_max - ts_min
    
#     dates = [ts_min+timedelta(days=i) for i in range(span.days+1)]

#     ## count how many join commands are in which day 
#     logs_per_day = defaultdict(lambda: 0)
#     for v in logs_ts:
#         logs_per_day[v] += 1
    
#     dates_count = []
#     count = 0
#     for d in dates:
#         count += logs_per_day[d]
#         dates_count.append(count)
    
#     return dates, dates_count


# def ircjoin_visualize(dates, dates_count):
#     plt.bar(dates,dates_count)
#     plt.show()

### Data export into CSV

In [10]:
# print('ircjoin...')
# for ln, l in zip(log_names, logs_join_divided):
#    fn = os.path.join(out_dir, ln, fileout_join_freq)
#    df_join = pd.DataFrame(columns=['channel','date','users_count'])
   
#    for l_k in l.keys():
#        log = l[l_k]
#        d_arr, dc_arr = ircjoin_compute(log)
#        # ircjoin_visualize(d, dc)
#        for d, dc in zip(d_arr,dc_arr):
#            df_join = df_join.append({'channel': l_k, 'date': d, 'users_count': dc}, ignore_index=True)
   
#    print(fn)
#    df_join.to_csv(fn, sep=';', encoding='utf-8')

### Reading exported all csv and merging it into one 

In [11]:
# print('ircjoin...')
# df_join = pd.DataFrame(columns=['channel','date','users_count', 'pcap', 'malicious'])
# for ln in log_names_mal:
#     fn = os.path.join(out_dir, ln, fileout_join_freq)
#     df_join_tmp = pd.read_csv(fn, sep=';', encoding='utf-8')
   
#     for i, df_el in df_join_tmp.iterrows():
#         df_join = df_join.append({'channel': df_el['channel'],
#                                   'date': df_el['date'],
#                                   'users_count': df_el['users_count'],
#                                   'pcap': ln,
#                                   'malicious': 1
#                                  }, ignore_index=True)
   
# for ln in log_names_benign:
#     fn = os.path.join(out_dir, ln, fileout_join_freq)
#     df_join_tmp = pd.read_csv(fn, sep=';', encoding='utf-8')
#     for i, df_el in df_join_tmp.iterrows():
#         df_join = df_join.append({'channel': df_el['channel'],
#                                       'date': df_el['date'],
#                                       'users_count': df_el['users_count'],
#                                       'pcap': ln,
#                                       'malicious': 0
#                                      }, ignore_index=True)
df_join = pd.read_csv(os.path.join(out_dir, 'join_freq_all.csv'))
df_join.drop('Unnamed: 0', axis=1, inplace=True)
df_join.head()

users_join_arr = []
for ln, logs_div in zip(log_names_mal, logs_privmsg_mal_divided):
    for channel in logs_div:
        m = df_join[(df_join['pcap'] == ln) & (df_join['channel'] == channel)]['users_count']
        users_join_arr.append(None if len(m) == 0 else max(m))

df_mal['users_join_max'] = users_join_arr
# df_mal.head()


users_join_arr = []
for ln, logs_div in zip(log_names_benign, logs_privmsg_benign_divided):
    for channel in logs_div:
        m = df_join[(df_join['pcap'] == ln) & (df_join['channel'] == channel)]['users_count']
        users_join_arr.append(None if len(m) == 0 else max(m))

df_benign['users_join_max'] = users_join_arr
df_benign.head()

pcap     channel  users_join_max lang msg_lev_dist_mean msg_lev_dist_std  \
0  irc1  #worldchat           689.0  NaN               NaN              NaN   
1  irc1    #amigacs            13.0  NaN               NaN              NaN   
2  irc1     #sscait            44.0  NaN               NaN              NaN   
3  irc1  #networker           820.0  NaN               NaN              NaN   
4  irc1   #red_rulz            27.0  NaN               NaN              NaN   

  msg_periodicity msg_frequency spec_chars_mean word_entropy active_users  \
0             NaN           NaN             NaN          NaN          NaN   
1             NaN           NaN             NaN          NaN          NaN   
2             NaN           NaN             NaN          NaN          NaN   
3             NaN           NaN             NaN          NaN          NaN   
4             NaN           NaN             NaN          NaN          NaN   

  onechannel_users_ratio network_info-num_services network_info-num_users  \
0                    NaN                       NaN                    NaN   
1                    NaN                       NaN                    NaN   
2                    NaN                       NaN                    NaN   
3                    NaN                       NaN                    NaN   
4                    NaN                       NaN                    NaN   

  malicious  
0       NaN  
1       NaN  
2       NaN  
3       NaN  
4       NaN

## Levenshtein Distance of Messages in Channel

In [12]:
def compute_levenshtein_distance(logs_msg):
    combs = itertools.combinations(logs_msg, 2)
    dist_lev_arr = []
    for msg1, msg2 in combs:
        dist_lev_arr.append(levenshtein_distance(msg1,msg2))
#     return dt_lev_arr

### Bubble plot

In [13]:
# n = len(logs_privmsg_divided)

# print('ircprivmsg..')

# def compute_lev_dist_per_channel(fn, l_k):
#     print('channel: ', l_k)
#     # compute levenshtein distance
#     logs_msg = [log['msg'] for log in logs_div[l_k]]
#     logs_lev_dist = compute_levenshtein_distance(logs_msg)
#     # compute number of msg's senders per channel
#     sources = set([log['source'] for log in logs_div[l_k]])
#     print('sources: ', len(sources))

#     df = pd.DataFrame([{'channel': l_k, 'num_sources': len(sources), 'lev_dist': logs_lev_dist}])
    

#     if not os.path.isfile(fn):
#         print('creating csv file....')
#         df.to_csv(fn, header='column_names')
#     else:
#         print('csv file exists.')
#         df.to_csv(fn, mode='a', header=False)

#     return df


# for ln, logs_div in zip(log_names_benign, logs_privmsg_divided):
#     with Pool() as pool:
#         fn = os.path.join(out_dir, ln, fileout_lev_dist)
#         # loop through channels            
#         data = pool.starmap(compute_lev_dist_per_channel, itertools.product([fn], logs_div.keys()))   
import ast
df_lev_mal = pd.read_csv(os.path.join(out_dir, 'lev_dist_mal.csv'))
df_lev_mal.drop('Unnamed: 0', axis=1, inplace=True)
df_lev_mal['lev_dist'] =  df_lev_mal['lev_dist'].apply(lambda x: ast.literal_eval(x))
# df_lev_mal.head()

df_mal['msg_lev_dist_mean'] = df_lev_mal['lev_dist'].apply(lambda x: np.mean(x))
df_mal['msg_lev_dist_std'] = df_lev_mal['lev_dist'].apply(lambda x: np.std(x))
df_mal.head()

/usr/local/lib/python3.7/site-packages/numpy/core/fromnumeric.py:3335: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/usr/local/lib/python3.7/site-packages/numpy/core/_methods.py:217: RuntimeWarning: Degrees of freedom <= 0 for slice
  keepdims=keepdims)


pcap   channel  users_join_max lang  msg_lev_dist_mean  msg_lev_dist_std  \
0   34  ##Summit              31  NaN          46.579578         27.772919   
1   42     #Runz               2  NaN                NaN               NaN   
2   51      #007              12  NaN          28.437374         15.612790   
3   51      #all               7  NaN          25.240929         19.280299   
4   51       #kz               2  NaN          33.619459         33.149611   

  msg_periodicity msg_frequency spec_chars_mean word_entropy active_users  \
0             NaN           NaN             NaN          NaN          NaN   
1             NaN           NaN             NaN          NaN          NaN   
2             NaN           NaN             NaN          NaN          NaN   
3             NaN           NaN             NaN          NaN          NaN   
4             NaN           NaN             NaN          NaN          NaN   

  onechannel_users_ratio network_info-num_services network_info-num_users  \
0                    NaN                       NaN                    NaN   
1                    NaN                       NaN                    NaN   
2                    NaN                       NaN                    NaN   
3                    NaN                       NaN                    NaN   
4                    NaN                       NaN                    NaN   

  malicious  
0       NaN  
1       NaN  
2       NaN  
3       NaN  
4       NaN

In [19]:
# means = []
# stds = []

for i, df_el in enumerate(pd.read_csv(os.path.join(out_dir, 'lev_dist_benign.csv'), skiprows=[72], chunksize=1)):
    print(i)
    if i == 71 or not np.isnan(df_benign.loc[i,'msg_lev_dist_mean']):
#         print('not nan, skipping..')
        continue 
    el = None
    try:
        el = np.array(ast.literal_eval(df_el['lev_dist'].iloc[0]))
        df_benign.loc[i, 'msg_lev_dist_mean'] = np.mean(el)
        df_benign.loc[i, 'msg_lev_dist_std'] = np.std(el)
        df_benign.to_csv(os.path.join(out_dir, 'lev_dist_benign2.csv'))
    except MemoryError:
        print('buu')
        del el
#  = means
# df_benign['lev_dist_std'] = stds
# df_benign.head()

pcap     channel  users_join_max     lang  msg_lev_dist_mean  \
0  irc1  #worldchat           689.0  English          30.621175   
1  irc1    #amigacs            13.0    Czech          43.947458   
2  irc1     #sscait            44.0  English          84.271868   
3  irc1  #networker           820.0  English           2.857143   
4  irc1   #red_rulz            27.0    Czech          42.808333   

   msg_lev_dist_std  msg_periodicity  msg_frequency  spec_chars_mean  \
0         16.520454         0.012571       0.022353         0.089418   
1         27.889922         0.008616       0.001194         0.174760   
2         40.064867         0.434539       0.000065         0.093750   
3          2.188405         1.000000       0.013757         0.076569   
4         35.959305         0.003511       0.003070         0.089700   

   word_entropy  active_users  onechannel_users_ratio  \
0     10.524316           201                0.945274   
1     10.192377             6                0.833333   
2      4.637199             1                0.000000   
3     10.312721            70                0.971429   
4      9.232857            11                0.818182   

   network_info-num_services  network_info-num_users  malicious  
0                          2                   30316          0  
1                          2                   30316          0  
2                          2                   30316          0  
3                          2                   30316          0  
4                          2                   30316          0

## Channel Language Recognition

In [15]:
## Create a text corpus for each file
def load_corpus(logs, pcap):
    corp_ch = set(filter(lambda x: len(x) > 2, chain.from_iterable(chain.from_iterable(map(lambda x: [re.findall(r"[a-zA-Z]+", w) for w in x['msg'].split()], logs)))))
    return corp_ch

## Malicious Samples

Compute message corpus per each channels

In [16]:
# logs_in = logs_privmsg_mal_divided
# load_corpus(logs_in)
corpus_df_mal = pd.DataFrame(columns=['pcap','corpus','lang'])
for ln, logs in zip(log_names_mal, logs_privmsg_mal_divided):
    for channel in logs.keys():
        corpus = load_corpus(logs[channel], ln)
        corpus_df_mal = corpus_df_mal.append({'pcap': ln, 'channel': channel, 'corpus': corpus}, ignore_index=True)

Detect languages

In [17]:
for i, c in corpus_df_mal.iterrows():
    pcap = c['pcap']
    text = " ".join(c['corpus'])
    lang = "Unidentified"
    if len(text) > 2:
        code = TextBlob(text).detect_language()
        lang = pycountry.languages.get(alpha_2=code).name
    corpus_df_mal.iloc[i]['lang'] =  lang

In [18]:
df_mal['lang'] = corpus_df_mal['lang']
df_mal.head()

pcap   channel  users_join_max          lang  msg_lev_dist_mean  \
0   34  ##Summit              31       English          46.579578   
1   42     #Runz               2  Unidentified                NaN   
2   51      #007              12       English          28.437374   
3   51      #all               7       English          25.240929   
4   51       #kz               2       English          33.619459   

   msg_lev_dist_std msg_periodicity msg_frequency spec_chars_mean  \
0         27.772919             NaN           NaN             NaN   
1               NaN             NaN           NaN             NaN   
2         15.612790             NaN           NaN             NaN   
3         19.280299             NaN           NaN             NaN   
4         33.149611             NaN           NaN             NaN   

  word_entropy active_users onechannel_users_ratio network_info-num_services  \
0          NaN          NaN                    NaN                       NaN   
1          NaN          NaN                    NaN                       NaN   
2          NaN          NaN                    NaN                       NaN   
3          NaN          NaN                    NaN                       NaN   
4          NaN          NaN                    NaN                       NaN   

  network_info-num_users malicious  
0                    NaN       NaN  
1                    NaN       NaN  
2                    NaN       NaN  
3                    NaN       NaN  
4                    NaN       NaN

### Plotbar - channels

In [19]:
# # # corpus_df.plot.pie(y='lang', figsize=(5,5))    
# fig = plt.figure(figsize=(10,10))

# myplot = corpus_df_mal['lang'].value_counts().plot(kind='bar', color =['blue','orange','gray'], title='(Malware Samples) Channel profiling - Language', alpha=0.7)
# import matplotlib.patches as mpatches
# POR = mpatches.Patch(color='orange', label= ",".join(list(corpus_df_mal[corpus_df_mal['lang'] == 'Portuguese']['channel'])))
# UN = mpatches.Patch(color='gray', label= ",".join(list(corpus_df_mal[corpus_df_mal['lang'] == 'Unidentified']['channel'])))
# ENG = mpatches.Patch(color='blue', label= ",".join(list(corpus_df_mal[corpus_df_mal['lang'] == 'English']['channel'])))
# myplot.legend(handles=[POR,UN,ENG])

# plt.xticks(rotation=0)

In [20]:
 corpus_df_mal['lang']

0         English
1    Unidentified
2         English
3         English
4         English
5      Portuguese
6         English
7         English
Name: lang, dtype: object

### Plotbar - pcaps

In [21]:
# # # corpus_df.plot.pie(y='lang', figsize=(5,5))    
# fig = plt.figure(figsize=(10,10))

# myplot = corpus_df_mal['lang'].value_counts().plot(kind='bar', color =['blue','orange','gray'], title='(Malware Samples) Channel profiling - Language', alpha=0.7)
# import matplotlib.patches as mpatches
# POR = mpatches.Patch(color='orange', label= ",".join(set(corpus_df_mal[corpus_df_mal['lang'] == 'Portuguese']['pcap'])))
# UN = mpatches.Patch(color='gray', label= ",".join(set(corpus_df_mal[corpus_df_mal['lang'] == 'Unidentified']['pcap'])))
# ENG = mpatches.Patch(color='blue', label= ",".join(set(corpus_df_mal[corpus_df_mal['lang'] == 'English']['pcap'])))
# myplot.legend(handles=[POR,UN,ENG])

# plt.xticks(rotation=0)

## Benign Samples

Compute message corpus per each channels

In [22]:
corpus_df_benign = pd.DataFrame(columns=['pcap','corpus','lang'])
for ln, logs in zip(log_names_benign, logs_privmsg_benign_divided):
    for channel in logs.keys():
        corpus = load_corpus(logs[channel], ln)
        corpus_df_benign = corpus_df_benign.append({'pcap': ln, 'channel': channel, 'corpus': corpus}, ignore_index=True)

Detect language

In [23]:
for i, c in corpus_df_benign.iterrows():
    pcap = c['pcap']
    text = " ".join(c['corpus'])
    lang = "Unidentified"
    if len(text) > 2:
        code = TextBlob(text).detect_language()
        lang = pycountry.languages.get(alpha_2=code).name
    corpus_df_benign.iloc[i]['lang'] =  lang

df_benign['lang'] = corpus_df_benign['lang']
df_benign.head()

pcap     channel  users_join_max     lang msg_lev_dist_mean  \
0  irc1  #worldchat           689.0  English               NaN   
1  irc1    #amigacs            13.0    Czech               NaN   
2  irc1     #sscait            44.0  English               NaN   
3  irc1  #networker           820.0  English               NaN   
4  irc1   #red_rulz            27.0    Czech               NaN   

  msg_lev_dist_std msg_periodicity msg_frequency spec_chars_mean word_entropy  \
0              NaN             NaN           NaN             NaN          NaN   
1              NaN             NaN           NaN             NaN          NaN   
2              NaN             NaN           NaN             NaN          NaN   
3              NaN             NaN           NaN             NaN          NaN   
4              NaN             NaN           NaN             NaN          NaN   

  active_users onechannel_users_ratio network_info-num_services  \
0          NaN                    NaN                       NaN   
1          NaN                    NaN                       NaN   
2          NaN                    NaN                       NaN   
3          NaN                    NaN                       NaN   
4          NaN                    NaN                       NaN   

  network_info-num_users malicious  
0                    NaN       NaN  
1                    NaN       NaN  
2                    NaN       NaN  
3                    NaN       NaN  
4                    NaN       NaN

### Plotbar - channels

In [24]:
# import random
# # corpus_df.plot.pie(y='lang', figsize=(5,5))    
# fig = plt.figure(figsize=(40,20))
# rgb = [(random.random(), random.random(), random.random()) for i in range(corpus_df_benign.shape[0])]
# langs = ['English', 'Czech', 'Spanish', 'French', 'Polish','Slovak',
#          'Romanian', 'Italian', 'Spanish', 'Igbo', 'French','Bosnian',
#          'Russian', 'Norwegian', 'Finnish', 'Turkish', 'Unidentified']
# myplot = corpus_df_benign['lang'].value_counts().plot(kind='bar', color=rgb, title='(Benign Samples) Channel profiling - Language', alpha=0.7)
# import matplotlib.patches as mpatches

# handle_arr = []
# for c, lang in zip(rgb, langs):
#     h = mpatches.Patch(color=c, label= ",".join(list(corpus_df_benign[corpus_df_benign['lang'] == lang]['channel'])))
#     handle_arr.append(h)

# myplot.legend(handles=handle_arr)

# plt.xticks(rotation=0)

### Plotbar - pcaps

In [25]:
# # corpus_df.plot.pie(y='lang', figsize=(5,5))    
# fig = plt.figure(figsize=(40,20))
# rgb = [(random.random(), random.random(), random.random()) for i in range(corpus_df_benign.shape[0])]
# langs = ['English', 'Czech', 'Spanish', 'French', 'Polish','Slovak',
#          'Romanian', 'Italian', 'Spanish', 'Igbo', 'French','Bosnian',
#          'Russian', 'Norwegian', 'Finnish', 'Turkish', 'Unidentified']
# myplot = corpus_df_benign['lang'].value_counts().plot(kind='bar', color=rgb, title='(Benign Samples) Channel profiling - Language', alpha=0.7)
# import matplotlib.patches as mpatches

# handle_arr = []
# for c, lang in zip(rgb, langs):
#     h = mpatches.Patch(color=c, label= ",".join(set(corpus_df_benign[corpus_df_benign['lang'] == lang]['pcap'])))
#     handle_arr.append(h)

# myplot.legend(handles=handle_arr)

# plt.xticks(rotation=0)

## Message periodicity

In [26]:
def compute_channel_periodicity(communication):
    """
    using Fast Fourier Transform to compute periodicity of messages in sessions
    @:return value in [0,1] interval - 0 means that messages are not periodic at all
    """

    if len(communication) < 3:
        return None

    t = list(map(lambda x: x['ts'].timestamp(), communication))
    td = np.asarray(list(map(lambda x: x[0] - x[1], zip(t[1:], t))))
    fft_res = np.absolute(np.fft.fft(td))
    T = fft_res.argmax() + 2

    rng_size = int(len(td) / T)
    td_T = [td[x * T:x * T + T] for x in range(rng_size)]
    td_T_avg = np.mean(td_T, 0)
    # ||td_t - td_avg ||2 / ||td_t||
    td_nmse = np.linalg.norm(td_T - td_T_avg) / np.linalg.norm(td_T)

    return 1 - td_nmse

### Malicious samples

In [27]:
per_arr = []
for ln, logs in zip(log_names_mal, logs_privmsg_mal_divided):
    for channel in logs.keys():
        per_arr.append(compute_channel_periodicity(logs[channel]))
df_mal['msg_periodicity'] = per_arr
df_mal.head()

/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:19: RuntimeWarning: invalid value encountered in double_scalars


pcap   channel  users_join_max          lang  msg_lev_dist_mean  \
0   34  ##Summit              31       English          46.579578   
1   42     #Runz               2  Unidentified                NaN   
2   51      #007              12       English          28.437374   
3   51      #all               7       English          25.240929   
4   51       #kz               2       English          33.619459   

   msg_lev_dist_std  msg_periodicity msg_frequency spec_chars_mean  \
0         27.772919         0.015128           NaN             NaN   
1               NaN              NaN           NaN             NaN   
2         15.612790         0.025560           NaN             NaN   
3         19.280299         0.002190           NaN             NaN   
4         33.149611              NaN           NaN             NaN   

  word_entropy active_users onechannel_users_ratio network_info-num_services  \
0          NaN          NaN                    NaN                       NaN   
1          NaN          NaN                    NaN                       NaN   
2          NaN          NaN                    NaN                       NaN   
3          NaN          NaN                    NaN                       NaN   
4          NaN          NaN                    NaN                       NaN   

  network_info-num_users malicious  
0                    NaN       NaN  
1                    NaN       NaN  
2                    NaN       NaN  
3                    NaN       NaN  
4                    NaN       NaN

### Benign Samples

In [28]:
per_arr = []
for ln, logs in zip(log_names_benign, logs_privmsg_benign_divided):
    for channel in logs.keys():
        per_arr.append(compute_channel_periodicity(logs[channel]))

df_benign['msg_periodicity'] = per_arr
df_benign.head()

/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:19: RuntimeWarning: invalid value encountered in double_scalars


pcap     channel  users_join_max     lang msg_lev_dist_mean  \
0  irc1  #worldchat           689.0  English               NaN   
1  irc1    #amigacs            13.0    Czech               NaN   
2  irc1     #sscait            44.0  English               NaN   
3  irc1  #networker           820.0  English               NaN   
4  irc1   #red_rulz            27.0    Czech               NaN   

  msg_lev_dist_std  msg_periodicity msg_frequency spec_chars_mean  \
0              NaN         0.012571           NaN             NaN   
1              NaN         0.008616           NaN             NaN   
2              NaN         0.434539           NaN             NaN   
3              NaN         1.000000           NaN             NaN   
4              NaN         0.003511           NaN             NaN   

  word_entropy active_users onechannel_users_ratio network_info-num_services  \
0          NaN          NaN                    NaN                       NaN   
1          NaN          NaN                    NaN                       NaN   
2          NaN          NaN                    NaN                       NaN   
3          NaN          NaN                    NaN                       NaN   
4          NaN          NaN                    NaN                       NaN   

  network_info-num_users malicious  
0                    NaN       NaN  
1                    NaN       NaN  
2                    NaN       NaN  
3                    NaN       NaN  
4                    NaN       NaN

## Message Frequency

In [29]:
def get_message_frequency(logs):
    if len(logs) < 2:
        return None
    t = list(map(lambda x: x['ts'].timestamp(), logs))
    try:
        return len(t)/(t[-1]-t[0])
    except ZeroDivisionError:
        return None

### Malicious Samples

In [30]:
freq_arr = []
for ln, logs in zip(log_names_mal, logs_privmsg_mal_divided):
    for channel in logs.keys():
        freq_arr.append(get_message_frequency(logs[channel]))
df_mal['msg_frequency'] = freq_arr
df_mal.head()

pcap   channel  users_join_max          lang  msg_lev_dist_mean  \
0   34  ##Summit              31       English          46.579578   
1   42     #Runz               2  Unidentified                NaN   
2   51      #007              12       English          28.437374   
3   51      #all               7       English          25.240929   
4   51       #kz               2       English          33.619459   

   msg_lev_dist_std  msg_periodicity  msg_frequency spec_chars_mean  \
0         27.772919         0.015128       0.001449             NaN   
1               NaN              NaN            NaN             NaN   
2         15.612790         0.025560       0.000189             NaN   
3         19.280299         0.002190       0.002409             NaN   
4         33.149611              NaN            NaN             NaN   

  word_entropy active_users onechannel_users_ratio network_info-num_services  \
0          NaN          NaN                    NaN                       NaN   
1          NaN          NaN                    NaN                       NaN   
2          NaN          NaN                    NaN                       NaN   
3          NaN          NaN                    NaN                       NaN   
4          NaN          NaN                    NaN                       NaN   

  network_info-num_users malicious  
0                    NaN       NaN  
1                    NaN       NaN  
2                    NaN       NaN  
3                    NaN       NaN  
4                    NaN       NaN

### Benign Samples

In [31]:
freq_arr = []
for ln, logs in zip(log_names_benign, logs_privmsg_benign_divided):
    for channel in logs.keys():
        freq_arr.append(get_message_frequency(logs[channel]))
df_benign['msg_frequency'] = freq_arr
df_benign.head()

pcap     channel  users_join_max     lang msg_lev_dist_mean  \
0  irc1  #worldchat           689.0  English               NaN   
1  irc1    #amigacs            13.0    Czech               NaN   
2  irc1     #sscait            44.0  English               NaN   
3  irc1  #networker           820.0  English               NaN   
4  irc1   #red_rulz            27.0    Czech               NaN   

  msg_lev_dist_std  msg_periodicity  msg_frequency spec_chars_mean  \
0              NaN         0.012571       0.022353             NaN   
1              NaN         0.008616       0.001194             NaN   
2              NaN         0.434539       0.000065             NaN   
3              NaN         1.000000       0.013757             NaN   
4              NaN         0.003511       0.003070             NaN   

  word_entropy active_users onechannel_users_ratio network_info-num_services  \
0          NaN          NaN                    NaN                       NaN   
1          NaN          NaN                    NaN                       NaN   
2          NaN          NaN                    NaN                       NaN   
3          NaN          NaN                    NaN                       NaN   
4          NaN          NaN                    NaN                       NaN   

  network_info-num_users malicious  
0                    NaN       NaN  
1                    NaN       NaN  
2                    NaN       NaN  
3                    NaN       NaN  
4                    NaN       NaN

## Special characters

In [32]:
def get_spec_chars_mean(logs):
    word_ch = list(chain.from_iterable(map(lambda x: x['msg'].split(), logs)))
    word_spec = map(lambda x: "".join(re.findall(r'[^A-Za-z]',x)), word_ch)
    spec_chars_count = sum(map(len, word_spec))
    chars_total_count = sum(map(len, word_ch))
    return spec_chars_count/chars_total_count

### Malicous Samples

In [33]:
spec_chars_arr = []
for ln, logs in zip(log_names_mal, logs_privmsg_mal_divided):
    for channel in logs.keys():
        spec_chars_arr.append(get_spec_chars_mean(logs[channel]))
        
df_mal['spec_chars_mean'] = spec_chars_arr
df_mal.head()

pcap   channel  users_join_max          lang  msg_lev_dist_mean  \
0   34  ##Summit              31       English          46.579578   
1   42     #Runz               2  Unidentified                NaN   
2   51      #007              12       English          28.437374   
3   51      #all               7       English          25.240929   
4   51       #kz               2       English          33.619459   

   msg_lev_dist_std  msg_periodicity  msg_frequency  spec_chars_mean  \
0         27.772919         0.015128       0.001449         0.290818   
1               NaN              NaN            NaN         0.000000   
2         15.612790         0.025560       0.000189         0.486271   
3         19.280299         0.002190       0.002409         0.599392   
4         33.149611              NaN            NaN         0.394054   

  word_entropy active_users onechannel_users_ratio network_info-num_services  \
0          NaN          NaN                    NaN                       NaN   
1          NaN          NaN                    NaN                       NaN   
2          NaN          NaN                    NaN                       NaN   
3          NaN          NaN                    NaN                       NaN   
4          NaN          NaN                    NaN                       NaN   

  network_info-num_users malicious  
0                    NaN       NaN  
1                    NaN       NaN  
2                    NaN       NaN  
3                    NaN       NaN  
4                    NaN       NaN

### Benign Samples

In [34]:
spec_chars_arr = []
for ln, logs in zip(log_names_benign, logs_privmsg_benign_divided):
    for channel in logs.keys():
        spec_chars_arr.append(get_spec_chars_mean(logs[channel]))
        
df_benign['spec_chars_mean'] = spec_chars_arr
df_benign.head()

pcap     channel  users_join_max     lang msg_lev_dist_mean  \
0  irc1  #worldchat           689.0  English               NaN   
1  irc1    #amigacs            13.0    Czech               NaN   
2  irc1     #sscait            44.0  English               NaN   
3  irc1  #networker           820.0  English               NaN   
4  irc1   #red_rulz            27.0    Czech               NaN   

  msg_lev_dist_std  msg_periodicity  msg_frequency  spec_chars_mean  \
0              NaN         0.012571       0.022353         0.089418   
1              NaN         0.008616       0.001194         0.174760   
2              NaN         0.434539       0.000065         0.093750   
3              NaN         1.000000       0.013757         0.076569   
4              NaN         0.003511       0.003070         0.089700   

  word_entropy active_users onechannel_users_ratio network_info-num_services  \
0          NaN          NaN                    NaN                       NaN   
1          NaN          NaN                    NaN                       NaN   
2          NaN          NaN                    NaN                       NaN   
3          NaN          NaN                    NaN                       NaN   
4          NaN          NaN                    NaN                       NaN   

  network_info-num_users malicious  
0                    NaN       NaN  
1                    NaN       NaN  
2                    NaN       NaN  
3                    NaN       NaN  
4                    NaN       NaN

## Word entropy

In [35]:
def get_word_entropy(logs):
    if len(logs) == 0:
        return None
    
    msg_word_count = defaultdict(lambda : 0)
    comm2 = []
    for log in logs:
        msg_words = log['msg'].split()
        for word in msg_words:
            msg_word_count[word] += 1

    _wordcounts = list(msg_word_count.values())
    p = _wordcounts / np.sum(_wordcounts)
    msg_word_entropy = -np.sum(p * np.log2(p))
    return msg_word_entropy

### Malicous Samples

In [36]:
word_entropy_arr = []
for ln, logs in zip(log_names_mal, logs_privmsg_mal_divided):
    for channel in logs.keys():
        word_entropy_arr.append(get_word_entropy(logs[channel]))

df_mal['word_entropy'] = word_entropy_arr
df_mal.head()

pcap   channel  users_join_max          lang  msg_lev_dist_mean  \
0   34  ##Summit              31       English          46.579578   
1   42     #Runz               2  Unidentified                NaN   
2   51      #007              12       English          28.437374   
3   51      #all               7       English          25.240929   
4   51       #kz               2       English          33.619459   

   msg_lev_dist_std  msg_periodicity  msg_frequency  spec_chars_mean  \
0         27.772919         0.015128       0.001449         0.290818   
1               NaN              NaN            NaN         0.000000   
2         15.612790         0.025560       0.000189         0.486271   
3         19.280299         0.002190       0.002409         0.599392   
4         33.149611              NaN            NaN         0.394054   

   word_entropy active_users onechannel_users_ratio network_info-num_services  \
0      8.103709          NaN                    NaN                       NaN   
1     -0.000000          NaN                    NaN                       NaN   
2      4.820940          NaN                    NaN                       NaN   
3      4.278526          NaN                    NaN                       NaN   
4      5.244206          NaN                    NaN                       NaN   

  network_info-num_users malicious  
0                    NaN       NaN  
1                    NaN       NaN  
2                    NaN       NaN  
3                    NaN       NaN  
4                    NaN       NaN

### Benign Samples

In [37]:
word_entropy_arr = []
for ln, logs in zip(log_names_benign, logs_privmsg_benign_divided):
    for channel in logs.keys():
        word_entropy_arr.append(get_word_entropy(logs[channel]))

df_benign['word_entropy'] = word_entropy_arr
df_benign.head()

pcap     channel  users_join_max     lang msg_lev_dist_mean  \
0  irc1  #worldchat           689.0  English               NaN   
1  irc1    #amigacs            13.0    Czech               NaN   
2  irc1     #sscait            44.0  English               NaN   
3  irc1  #networker           820.0  English               NaN   
4  irc1   #red_rulz            27.0    Czech               NaN   

  msg_lev_dist_std  msg_periodicity  msg_frequency  spec_chars_mean  \
0              NaN         0.012571       0.022353         0.089418   
1              NaN         0.008616       0.001194         0.174760   
2              NaN         0.434539       0.000065         0.093750   
3              NaN         1.000000       0.013757         0.076569   
4              NaN         0.003511       0.003070         0.089700   

   word_entropy active_users onechannel_users_ratio network_info-num_services  \
0     10.524316          NaN                    NaN                       NaN   
1     10.192377          NaN                    NaN                       NaN   
2      4.637199          NaN                    NaN                       NaN   
3     10.312721          NaN                    NaN                       NaN   
4      9.232857          NaN                    NaN                       NaN   

  network_info-num_users malicious  
0                    NaN       NaN  
1                    NaN       NaN  
2                    NaN       NaN  
3                    NaN       NaN  
4                    NaN       NaN

## Channel - Active Users

In [64]:
def get_active_users(logs):
    active_users = set(map(lambda x: x['source'], logs))
    return len(active_users)

### Malicous Samples

In [65]:
active_users_arr = []
for ln, logs in zip(log_names_mal, logs_privmsg_mal_divided):
    for channel in logs.keys():
        active_users_arr.append(get_active_users(logs[channel]))

df_mal['active_users'] = active_users_arr
df_mal.head()

pcap   channel  users_join_max          lang  msg_lev_dist_mean  \
0   34  ##Summit              31       English          46.579578   
1   42     #Runz               2  Unidentified                NaN   
2   51      #007              12       English          28.437374   
3   51      #all               7       English          25.240929   
4   51       #kz               2       English          33.619459   

   msg_lev_dist_std  msg_periodicity  msg_frequency  spec_chars_mean  \
0         27.772919         0.015128       0.001449         0.290818   
1               NaN              NaN            NaN         0.000000   
2         15.612790         0.025560       0.000189         0.486271   
3         19.280299         0.002190       0.002409         0.599392   
4         33.149611              NaN            NaN         0.394054   

   word_entropy  active_users  onechannel_users_ratio  \
0      8.103709             6                    1.00   
1     -0.000000             1                    1.00   
2      4.820940             3                    0.00   
3      4.278526             4                    0.25   
4      5.244206             2                    0.00   

   network_info-num_services  network_info-num_users  malicious  
0                          0                       1          1  
1                          0                     233          1  
2                          0                       1          1  
3                          0                       1          1  
4                          0                       1          1

### Benign Samples

In [66]:
active_users_arr = []
for ln, logs in zip(log_names_benign, logs_privmsg_benign_divided):
    for channel in logs.keys():
        active_users_arr.append(get_active_users(logs[channel]))
        

df_benign['active_users'] = active_users_arr
df_benign.head()

pcap     channel  users_join_max     lang msg_lev_dist_mean  \
0  irc1  #worldchat           689.0  English               NaN   
1  irc1    #amigacs            13.0    Czech               NaN   
2  irc1     #sscait            44.0  English               NaN   
3  irc1  #networker           820.0  English               NaN   
4  irc1   #red_rulz            27.0    Czech               NaN   

  msg_lev_dist_std  msg_periodicity  msg_frequency  spec_chars_mean  \
0              NaN         0.012571       0.022353         0.089418   
1              NaN         0.008616       0.001194         0.174760   
2              NaN         0.434539       0.000065         0.093750   
3              NaN         1.000000       0.013757         0.076569   
4              NaN         0.003511       0.003070         0.089700   

   word_entropy  active_users  onechannel_users_ratio  \
0     10.524316           201                0.945274   
1     10.192377             6                0.833333   
2      4.637199             1                0.000000   
3     10.312721            70                0.971429   
4      9.232857            11                0.818182   

   network_info-num_services  network_info-num_users  malicious  
0                          2                   30316          0  
1                          2                   30316          0  
2                          2                   30316          0  
3                          2                   30316          0  
4                          2                   30316          0

## Network Info - Number of Services

In [67]:
def get_num_services(logs):
    try:
        num_services = list(map(lambda x: x['services'], logs))
        return max(num_services)
    except:
        return None

### Malicious Samples

In [68]:
num_services_arr = []
for ln, l in zip(log_names_mal, logs_networkinfo_mal):
    rows = df_mal[df_mal['pcap'] == ln]
    df_mal.loc[(df_mal['pcap'] == ln), 'network_info-num_services'] = get_num_services(l)

df_mal.head()

pcap   channel  users_join_max          lang  msg_lev_dist_mean  \
0   34  ##Summit              31       English          46.579578   
1   42     #Runz               2  Unidentified                NaN   
2   51      #007              12       English          28.437374   
3   51      #all               7       English          25.240929   
4   51       #kz               2       English          33.619459   

   msg_lev_dist_std  msg_periodicity  msg_frequency  spec_chars_mean  \
0         27.772919         0.015128       0.001449         0.290818   
1               NaN              NaN            NaN         0.000000   
2         15.612790         0.025560       0.000189         0.486271   
3         19.280299         0.002190       0.002409         0.599392   
4         33.149611              NaN            NaN         0.394054   

   word_entropy  active_users  onechannel_users_ratio  \
0      8.103709             6                    1.00   
1     -0.000000             1                    1.00   
2      4.820940             3                    0.00   
3      4.278526             4                    0.25   
4      5.244206             2                    0.00   

   network_info-num_services  network_info-num_users  malicious  
0                        0.0                       1          1  
1                        0.0                     233          1  
2                        0.0                       1          1  
3                        0.0                       1          1  
4                        0.0                       1          1

### Benign Samples

In [69]:
num_services_arr = []
for ln, l in zip(log_names_benign, logs_networkinfo_benign):
    df_benign.loc[(df_benign['pcap'] == ln), 'network_info-num_services'] = get_num_services(l)
    
df_benign.head()

pcap     channel  users_join_max     lang msg_lev_dist_mean  \
0  irc1  #worldchat           689.0  English               NaN   
1  irc1    #amigacs            13.0    Czech               NaN   
2  irc1     #sscait            44.0  English               NaN   
3  irc1  #networker           820.0  English               NaN   
4  irc1   #red_rulz            27.0    Czech               NaN   

  msg_lev_dist_std  msg_periodicity  msg_frequency  spec_chars_mean  \
0              NaN         0.012571       0.022353         0.089418   
1              NaN         0.008616       0.001194         0.174760   
2              NaN         0.434539       0.000065         0.093750   
3              NaN         1.000000       0.013757         0.076569   
4              NaN         0.003511       0.003070         0.089700   

   word_entropy  active_users  onechannel_users_ratio  \
0     10.524316           201                0.945274   
1     10.192377             6                0.833333   
2      4.637199             1                0.000000   
3     10.312721            70                0.971429   
4      9.232857            11                0.818182   

   network_info-num_services  network_info-num_users  malicious  
0                          2                   30316          0  
1                          2                   30316          0  
2                          2                   30316          0  
3                          2                   30316          0  
4                          2                   30316          0

## Network Info - Number of Users

In [70]:
def get_num_users(logs):
    try:
        num_services = list(map(lambda x: x['users'], logs))
        return max(num_services)
    except:
        return None

### Malicious Samples

In [71]:
num_users_arr = []
for ln, l in zip(log_names_mal, logs_networkinfo_mal):
    df_mal.loc[(df_mal['pcap'] == ln), 'network_info-num_users'] = get_num_users(l)
    
df_mal.head()

pcap   channel  users_join_max          lang  msg_lev_dist_mean  \
0   34  ##Summit              31       English          46.579578   
1   42     #Runz               2  Unidentified                NaN   
2   51      #007              12       English          28.437374   
3   51      #all               7       English          25.240929   
4   51       #kz               2       English          33.619459   

   msg_lev_dist_std  msg_periodicity  msg_frequency  spec_chars_mean  \
0         27.772919         0.015128       0.001449         0.290818   
1               NaN              NaN            NaN         0.000000   
2         15.612790         0.025560       0.000189         0.486271   
3         19.280299         0.002190       0.002409         0.599392   
4         33.149611              NaN            NaN         0.394054   

   word_entropy  active_users  onechannel_users_ratio  \
0      8.103709             6                    1.00   
1     -0.000000             1                    1.00   
2      4.820940             3                    0.00   
3      4.278526             4                    0.25   
4      5.244206             2                    0.00   

   network_info-num_services  network_info-num_users  malicious  
0                        0.0                     1.0          1  
1                        0.0                   233.0          1  
2                        0.0                     1.0          1  
3                        0.0                     1.0          1  
4                        0.0                     1.0          1

### Benign Samples

In [72]:
num_users_arr = []
for ln, l in zip(log_names_benign, logs_networkinfo_benign):
    df_benign.loc[(df_benign['pcap'] == ln), 'network_info-num_users'] = get_num_users(l)
    
df_benign.head()

pcap     channel  users_join_max     lang msg_lev_dist_mean  \
0  irc1  #worldchat           689.0  English               NaN   
1  irc1    #amigacs            13.0    Czech               NaN   
2  irc1     #sscait            44.0  English               NaN   
3  irc1  #networker           820.0  English               NaN   
4  irc1   #red_rulz            27.0    Czech               NaN   

  msg_lev_dist_std  msg_periodicity  msg_frequency  spec_chars_mean  \
0              NaN         0.012571       0.022353         0.089418   
1              NaN         0.008616       0.001194         0.174760   
2              NaN         0.434539       0.000065         0.093750   
3              NaN         1.000000       0.013757         0.076569   
4              NaN         0.003511       0.003070         0.089700   

   word_entropy  active_users  onechannel_users_ratio  \
0     10.524316           201                0.945274   
1     10.192377             6                0.833333   
2      4.637199             1                0.000000   
3     10.312721            70                0.971429   
4      9.232857            11                0.818182   

   network_info-num_services  network_info-num_users  malicious  
0                          2                   30316          0  
1                          2                   30316          0  
2                          2                   30316          0  
3                          2                   30316          0  
4                          2                   30316          0

## One-channel users Ratio

In [73]:
def compute_num_channels(user, users_per_channels):
    count = 0
    for ch in users_per_channels.keys():
        if user in users_per_channels[ch]:
            count += 1
    return count

### Malicious Samples

In [74]:
onechannel_users_arr = []
for ln, logs in zip(log_names_mal, logs_privmsg_mal_divided):
    users = set()
    users_channel_count = {}
    users_per_channel = {}
    for channel in logs.keys():
        users_per_channel[channel] = set(map(lambda x: x['source'], logs[channel]))
        users = users.union(users_per_channel[channel])
    
    for u in users:
        users_channel_count[u] = compute_num_channels(u, users_per_channel)
    
    for channel in logs.keys():
        onechannel_users_count = 0
        for u in users_per_channel[channel]:
            if users_channel_count[u] == 1:
                onechannel_users_count += 1
        onechannel_ratio = 0
        if len(users_per_channel[channel]):
            onechannel_ratio = onechannel_users_count/len(users_per_channel[channel])
        onechannel_users_arr.append(onechannel_ratio)

df_mal['onechannel_users_ratio'] = onechannel_users_arr
df_mal.head()

pcap   channel  users_join_max          lang  msg_lev_dist_mean  \
0   34  ##Summit              31       English          46.579578   
1   42     #Runz               2  Unidentified                NaN   
2   51      #007              12       English          28.437374   
3   51      #all               7       English          25.240929   
4   51       #kz               2       English          33.619459   

   msg_lev_dist_std  msg_periodicity  msg_frequency  spec_chars_mean  \
0         27.772919         0.015128       0.001449         0.290818   
1               NaN              NaN            NaN         0.000000   
2         15.612790         0.025560       0.000189         0.486271   
3         19.280299         0.002190       0.002409         0.599392   
4         33.149611              NaN            NaN         0.394054   

   word_entropy  active_users  onechannel_users_ratio  \
0      8.103709             6                    1.00   
1     -0.000000             1                    1.00   
2      4.820940             3                    0.00   
3      4.278526             4                    0.25   
4      5.244206             2                    0.00   

   network_info-num_services  network_info-num_users  malicious  
0                        0.0                     1.0          1  
1                        0.0                   233.0          1  
2                        0.0                     1.0          1  
3                        0.0                     1.0          1  
4                        0.0                     1.0          1

### Benign Samples

In [75]:
onechannel_users_arr = []
for ln, logs in zip(log_names_benign, logs_privmsg_benign_divided):
    users = set()
    users_channel_count = {}
    users_per_channel = {}
    for channel in logs.keys():
        users_per_channel[channel] = set(map(lambda x: x['source'], logs[channel]))
        users = users.union(users_per_channel[channel])
    
    for u in users:
        users_channel_count[u] = compute_num_channels(u, users_per_channel)
    
    for channel in logs.keys():
        onechannel_users_count = 0
        for u in users_per_channel[channel]:
            if users_channel_count[u] == 1:
                onechannel_users_count += 1
        onechannel_ratio = 0
        if len(users_per_channel[channel]):
            onechannel_ratio = onechannel_users_count/len(users_per_channel[channel])
        onechannel_users_arr.append(onechannel_ratio)

df_benign['onechannel_users_ratio'] = onechannel_users_arr
df_benign.head()

pcap     channel  users_join_max     lang msg_lev_dist_mean  \
0  irc1  #worldchat           689.0  English               NaN   
1  irc1    #amigacs            13.0    Czech               NaN   
2  irc1     #sscait            44.0  English               NaN   
3  irc1  #networker           820.0  English               NaN   
4  irc1   #red_rulz            27.0    Czech               NaN   

  msg_lev_dist_std  msg_periodicity  msg_frequency  spec_chars_mean  \
0              NaN         0.012571       0.022353         0.089418   
1              NaN         0.008616       0.001194         0.174760   
2              NaN         0.434539       0.000065         0.093750   
3              NaN         1.000000       0.013757         0.076569   
4              NaN         0.003511       0.003070         0.089700   

   word_entropy  active_users  onechannel_users_ratio  \
0     10.524316           201                0.945274   
1     10.192377             6                0.833333   
2      4.637199             1                0.000000   
3     10.312721            70                0.971429   
4      9.232857            11                0.818182   

   network_info-num_services  network_info-num_users  malicious  
0                          2                   30316          0  
1                          2                   30316          0  
2                          2                   30316          0  
3                          2                   30316          0  
4                          2                   30316          0

## Exporting DataFrames into CSV

In [76]:
df_mal.to_csv(os.path.join(out_dir, 'irc_channel_features_malicious.csv'))
df_benign.to_csv(os.path.join(out_dir, 'irc_channel_features_benign.csv'))

In [81]:
df_mal['malicious'] = 1
df_benign['malicious'] = 0
df_all = df_mal.append(df_benign, ignore_index=True)
df_all.to_csv(os.path.join(out_dir,'irc_channel_features_all.csv'))

In [78]:
print(df_mal.columns)
print(df_benign.columns)

Index(['pcap', 'channel', 'users_join_max', 'lang', 'msg_lev_dist_mean',
       'msg_lev_dist_std', 'msg_periodicity', 'msg_frequency',
       'spec_chars_mean', 'word_entropy', 'active_users',
       'onechannel_users_ratio', 'network_info-num_services',
       'network_info-num_users', 'malicious'],
      dtype='object')
Index(['pcap', 'channel', 'users_join_max', 'lang', 'msg_lev_dist_mean',
       'msg_lev_dist_std', 'msg_periodicity', 'msg_frequency',
       'spec_chars_mean', 'word_entropy', 'active_users',
       'onechannel_users_ratio', 'network_info-num_services',
       'network_info-num_users', 'malicious'],
      dtype='object')


In [80]:
df_all

pcap       channel  users_join_max          lang msg_lev_dist_mean  \
0     34      ##Summit            31.0       English           46.5796   
1     42         #Runz             2.0  Unidentified               NaN   
2     51          #007            12.0       English           28.4374   
3     51          #all             7.0       English           25.2409   
4     51           #kz             2.0       English           33.6195   
..   ...           ...             ...           ...               ...   
76  irc1  #czestochowa           169.0        French               NaN   
77  irc1      #Romania             NaN       Spanish               NaN   
78  irc1    #funkychat             4.0       Finnish               NaN   
79  irc1            #z            60.0      Romanian               NaN   
80  irc1    #makedonia           381.0  Unidentified               NaN   

   msg_lev_dist_std  msg_periodicity  msg_frequency  spec_chars_mean  \
0           27.7729         0.015128       0.001449         0.290818   
1               NaN              NaN            NaN         0.000000   
2           15.6128         0.025560       0.000189         0.486271   
3           19.2803         0.002190       0.002409         0.599392   
4           33.1496              NaN            NaN         0.394054   
..              ...              ...            ...              ...   
76              NaN              NaN   16946.682828         0.230769   
77              NaN         0.074180       0.049511         0.031746   
78              NaN              NaN            NaN         0.000000   
79              NaN              NaN   35098.778243         0.200000   
80              NaN         1.000000   52560.200501         0.000000   

    word_entropy  active_users  onechannel_users_ratio  \
0       8.103709             6                    1.00   
1      -0.000000             1                    1.00   
2       4.820940             3                    0.00   
3       4.278526             4                    0.25   
4       5.244206             2                    0.00   
..           ...           ...                     ...   
76      1.000000             1                    1.00   
77      3.169925             1                    0.00   
78      2.000000             1                    0.00   
79      1.000000             1                    0.00   
80     -0.000000             1                    1.00   

    network_info-num_services  network_info-num_users  malicious  
0                         0.0                     1.0          1  
1                         0.0                   233.0          1  
2                         0.0                     1.0          1  
3                         0.0                     1.0          1  
4                         0.0                     1.0          1  
..                        ...                     ...        ...  
76                        2.0                 30316.0          0  
77                        2.0                 30316.0          0  
78                        2.0                 30316.0          0  
79                        2.0                 30316.0          0  
80                        2.0                 30316.0          0  

[81 rows x 15 columns]

In [21]:
df_benign = pd.read_csv(os.path.join(out_dir,'irc_channel_features_benign.csv'))
df_benign.drop(['Unnamed: 0'], axis=1, inplace=True)
df_mal = pd.read_csv(os.path.join(out_dir, 'irc_channel_features_malicious.csv'))
df_mal.drop(['Unnamed: 0'], axis=1, inplace=True)

df_all = df_mal.append(df_benign, ignore_index=True)
df_all.to_csv(os.path.join(out_dir,'irc_channel_features_all.csv'))